**This notebook is for demonstration purposes only. The focus is on illustrating the ideas rather than code implementation details.** For pseudocode and well-organized implementations, please refer to the textbook and the AIMA Python repository:
https://github.com/aimacode/aima-python/tree/master

## Find path: from A to B

* Greedy Best-First Search
* Heuristic function: manhattan distance

**❓Q: Which block is closer to B, C or D? (if consider manhattan distance as $h(n)$)**

<img src="images/heuristic_abcd.png" width="500px"> 
<img src="images/heuristic_manhattan.png" width="500px"> 

In [23]:
import numpy as np
import heapq
import matplotlib.pyplot as plt
from matplotlib.patches import Rectangle
from matplotlib.animation import FuncAnimation
from IPython.display import HTML, display


In [24]:

# ----------------------------
# 1) Environment (7x12)
# ----------------------------
H, W = 7, 12
A = (6, 0)
B = (0, 11)
C = (4, 1)
D = (2, 7)

gray_blocks = [
    (0,1),(0,3),(0,5),(0,6),(0,7),(0,10),
    (1,1),(1,3),(1,7),(1,9),(1,10),
    (2,3),(2,5),(2,9),(2,10),
    (3,0),(3,2),(3,3),(3,5),(3,7),(3,9),(3,10),
    (4,0),(4,5),(4,7),
    (5,0),(5,1),(5,2),(5,4),(5,5),
    (5,7),(5,8),(5,9),(5,10),(5,11),
    (6,4),(6,5)
]

grid = np.zeros((H, W), dtype=int)  # 0 free, 1 wall
for r, c in gray_blocks:
    grid[r, c] = 1

# Ensure special cells are free
for rc in [A, B, C, D]:
    grid[rc] = 0

def manhattan(p, q):
    return abs(p[0]-q[0]) + abs(p[1]-q[1])

def neighbors4(p):
    r, c = p
    for dr, dc in [(-1,0),(1,0),(0,-1),(0,1)]:
        rr, cc = r+dr, c+dc
        if 0 <= rr < H and 0 <= cc < W and grid[rr, cc] == 0:
            yield (rr, cc)


In [25]:

# ----------------------------
# 2) Greedy Best-First Search (priority = h only)
# ----------------------------
def greedy_best_first(start, goal):
    pq = []
    counter = 0
    heapq.heappush(pq, (manhattan(start, goal), counter, start))
    counter += 1

    came_from = {start: None}
    expanded_order = []
    expanded_set = set()
    frames = []           # store per-step snapshots

    def snapshot(current, note=""):
        # frontier nodes for debugging/teaching (not required, but useful)
        frontier_nodes = [n for _,__,n in pq if n not in expanded_set]
        frames.append({
            "current": current,
            "closed": set(expanded_set),
            "came_from": dict(came_from),
            "frontier": set(frontier_nodes),
            "note": note
        })

    snapshot(start, "Initialize: push A with f=h(A) because g(A)=0")

    while pq:
        h, _, node = heapq.heappop(pq)
        if node in expanded_set:
            continue
        expanded_set.add(node)
        expanded_order.append(node)
        snapshot(node, f"Pop node with min f. current={node}, f=h (h={manhattan(node,goal)})")

        if node == goal:
            snapshot(node, "Goal reached!")
            break

        for nb in neighbors4(node):
            if nb in expanded_set or nb in came_from:
                continue
            came_from[nb] = node
            heapq.heappush(pq, (manhattan(nb, goal), counter, nb))
            counter += 1
        
        snapshot(node, "Expand current; relax neighbors (push with f=h)")

    # reconstruct path (via parents)
    path = []
    if goal in came_from:
        cur = goal
        while cur is not None:
            path.append(cur)
            cur = came_from[cur]
        path.reverse()

    return expanded_order, path, frames

expanded_order, path, frames = greedy_best_first(A, B)

print("Heuristic comparison:")
print("h(C) =", manhattan(C, B), " | h(D) =", manhattan(D, B))
print("Expanded nodes:", len(expanded_order))
print("Found path length (cost):", (len(path)-1) if path else None)


Heuristic comparison:
h(C) = 14  | h(D) = 6
Expanded nodes: 28
Found path length (cost): 23


In [26]:

# ----------------------------
# 3) Visualization helpers
# ----------------------------
def draw_cell(ax, r, c, face, edge="#cccccc", lw=0.8, z=1):
    ax.add_patch(Rectangle((c, r), 1, 1, facecolor=face, edgecolor=edge, linewidth=lw, zorder=z))

def draw_label(ax, pos, label, color):
    r, c = pos
    draw_cell(ax, r, c, color, z=6)
    ax.text(c+0.5, r+0.62, label, ha="center", va="center",
            fontsize=20, color="white", fontweight="bold", zorder=7)

def render_state(ax, expanded_up_to_idx, current_idx, show_h=True, show_path_after_goal=True):
    ax.clear()
    ax.set_aspect("equal")
    ax.set_xlim(0, W)
    ax.set_ylim(H, 0)
    ax.axis("off")

    # background
    ax.figure.patch.set_facecolor("black")
    ax.set_facecolor("black")

    # heuristic table (only on free cells)
    h_table = np.full((H, W), "", dtype=object)
    if show_h:
        for r in range(H):
            for c in range(W):
                if grid[r, c] == 0:
                    h_table[r, c] = str(manhattan((r, c), B))

    # draw base grid
    for r in range(H):
        for c in range(W):
            if grid[r, c] == 1:
                face = "#555555"   # gray blocks
            else:
                face = "#000000"   # free
            draw_cell(ax, r, c, face)

            if show_h and grid[r, c] == 0 and (r, c) != B:
                ax.text(c+0.5, r+0.55, h_table[r, c],
                        ha="center", va="center", fontsize=16,
                        color="white", fontweight="bold", zorder=2)

    # expanded nodes (yellow)
    expanded_now = expanded_order[:expanded_up_to_idx+1]
    for (r, c) in expanded_now:
        if (r, c) not in [A, B, C, D]:
            draw_cell(ax, r, c, "#ffd84d", z=3)
            if show_h:
                ax.text(c+0.5, r+0.55, h_table[r, c],
                        ha="center", va="center", fontsize=16,
                        color="black", fontweight="bold", zorder=4)

    # current node outline
    if 0 <= current_idx < len(expanded_order):
        cr, cc = expanded_order[current_idx]
        ax.add_patch(Rectangle((cc, cr), 1, 1, fill=False, edgecolor="white", linewidth=3, zorder=8))

    # optional: after goal reached, overlay final found path in cyan
    reached = (expanded_order[min(expanded_up_to_idx, len(expanded_order)-1)] == B)
    if show_path_after_goal and reached and path:
        for (r, c) in path:
            if (r, c) not in [A, B]:
                ax.add_patch(Rectangle((c, r), 1, 1, facecolor="#00d0ff", edgecolor="#00d0ff", linewidth=0.0, zorder=2.5))
                if show_h:
                    ax.text(c+0.5, r+0.55, h_table[r, c],
                            ha="center", va="center", fontsize=16,
                            color="black", fontweight="bold", zorder=4)

    # labels on top
    draw_label(ax, A, "A", "#b01515")
    draw_label(ax, B, "B", "#0b6a1f")
    draw_label(ax, C, "C", "#0a72a8")
    draw_label(ax, D, "D", "#0a72a8")

    # title text
    ax.text(0.02, 1.08,
            f"Greedy Best-First Search (priority = Manhattan h) | step {current_idx+1}/{len(expanded_order)}",
            transform=ax.transAxes, fontsize=18, color="black")
    ax.text(0.02, 1.03, frames[current_idx]["note"], transform=ax.transAxes, fontsize=12, color="black")

# ----------------------------
# 4) Animate: one step per second
# ----------------------------
fig, ax = plt.subplots(figsize=(11, 6))

def update(frame):
    render_state(ax, expanded_up_to_idx=frame, current_idx=frame, show_h=True, show_path_after_goal=True)

anim = FuncAnimation(fig, update, frames=len(expanded_order), interval=1000, repeat=False)

plt.close(fig)
display(HTML(anim.to_jshtml()))


## Another game: still from A to B
<img src="images/heuristic_another_game.png" width="500px"> 

In [27]:
# ----------------------------
# Environment (7x12) - NEW PROBLEM
# ----------------------------
H, W = 7, 12
A = (6, 0)
B = (0, 11)

gray_blocks = [
    (0,0),
    (1,0),(1,2),(1,3),(1,4),(1,5),
    (1,6),(1,7),(1,8),(1,9),(1,10),
    (2,0),(2,2),(2,10),
    (3,0),(3,2),(3,4),(3,5),
    (3,6),(3,7),(3,8),(3,10),
    (4,0),(4,4),(4,10),
    (5,0),(5,1),(5,2),(5,4),
    (5,6),(5,7),(5,8),(5,9),(5,10),
    (6,4)
]

grid = np.zeros((H, W), dtype=int)  # 0 free, 1 wall
for r, c in gray_blocks:
    grid[r, c] = 1

my_labels = [A,B]
# Ensure special cells are free
for rc in my_labels:
    grid[rc] = 0

In [28]:
expanded_order, path, frames = greedy_best_first(A, B)

print("Heuristic comparison:")
print("h(C) =", manhattan(C, B), " | h(D) =", manhattan(D, B))
print("Expanded nodes:", len(expanded_order))
print("Found path length (cost):", (len(path)-1) if path else None)

Heuristic comparison:
h(C) = 14  | h(D) = 6
Expanded nodes: 34
Found path length (cost): 33


In [30]:
def render_state(ax, expanded_up_to_idx, current_idx, show_h=True, show_path_after_goal=True):
    ax.clear()
    ax.set_aspect("equal")
    ax.set_xlim(0, W)
    ax.set_ylim(H, 0)
    ax.axis("off")

    # background
    ax.figure.patch.set_facecolor("black")
    ax.set_facecolor("black")

    # heuristic table (only on free cells)
    h_table = np.full((H, W), "", dtype=object)
    if show_h:
        for r in range(H):
            for c in range(W):
                if grid[r, c] == 0:
                    h_table[r, c] = str(manhattan((r, c), B))

    # draw base grid
    for r in range(H):
        for c in range(W):
            if grid[r, c] == 1:
                face = "#555555"   # gray blocks
            else:
                face = "#000000"   # free
            draw_cell(ax, r, c, face)

            if show_h and grid[r, c] == 0 and (r, c) != B:
                ax.text(c+0.5, r+0.55, h_table[r, c],
                        ha="center", va="center", fontsize=16,
                        color="white", fontweight="bold", zorder=2)

    # expanded nodes (yellow)
    expanded_now = expanded_order[:expanded_up_to_idx+1]
    for (r, c) in expanded_now:
        if (r, c) not in [A, B]:
            draw_cell(ax, r, c, "#ffd84d", z=3)
            if show_h:
                ax.text(c+0.5, r+0.55, h_table[r, c],
                        ha="center", va="center", fontsize=16,
                        color="black", fontweight="bold", zorder=4)

    # current node outline
    if 0 <= current_idx < len(expanded_order):
        cr, cc = expanded_order[current_idx]
        ax.add_patch(Rectangle((cc, cr), 1, 1, fill=False, edgecolor="white", linewidth=3, zorder=8))

    # optional: after goal reached, overlay final found path in cyan
    reached = (expanded_order[min(expanded_up_to_idx, len(expanded_order)-1)] == B)
    if show_path_after_goal and reached and path:
        for (r, c) in path:
            if (r, c) not in [A, B]:
                ax.add_patch(Rectangle((c, r), 1, 1, facecolor="#00d0ff", edgecolor="#00d0ff", linewidth=0.0, zorder=2.5))
                if show_h:
                    ax.text(c+0.5, r+0.55, h_table[r, c],
                            ha="center", va="center", fontsize=16,
                            color="black", fontweight="bold", zorder=4)

    # labels on top
    draw_label(ax, A, "A", "#b01515")
    draw_label(ax, B, "B", "#0b6a1f")

    # title text
    ax.text(0.02, 1.08,
            f"Greedy Best-First Search (priority = Manhattan h) | step {current_idx+1}/{len(expanded_order)}",
            transform=ax.transAxes, fontsize=18, color="black")
    ax.text(0.02, 1.03, frames[current_idx]["note"], transform=ax.transAxes, fontsize=12, color="black")

# ----------------------------
# 4) Animate: one step per second
# ----------------------------
fig, ax = plt.subplots(figsize=(11, 6))

anim = FuncAnimation(fig, update, frames=len(expanded_order), interval=1000, repeat=False)

plt.close(fig)
display(HTML(anim.to_jshtml()))